# Magnetic Resonance Imaging 

## Looking Ahead

In the previous example, we verified that an example MR image from a dataset was sparse in the wavelet domain, after we transformed it from the spatial domain. In this example, we will exploit this sparsity in order to recover the MR image from compressive measurements. Recall that MR images are, at acquisition time, obtained in the Fourier domain; this has implications for the measurement map that we construct in a compressed sensing setup. Please review the homework writeup for a discussion of these issues and a justification for the sensing model we implement below.

## Loading the Data

We use the same code from the previous notebook to load in the data. As before, we will focus on a single sagittarial slice of the patient's anatomical data.

In [1]:
## Install AWS CLI tools
!pip install awscli
## Prepare data directory
import os
os.chdir('/content')
!mkdir bold5000
os.chdir('/content/bold5000')

## Grab the data
#!aws s3 sync --no-sign-request --exclude "*" --include "*06*" s3://openneuro.org/ds001499/derivatives/fmriprep/sub-CSI3/ses-13/func/ /content/bold5000/sub-CSI3_ses-13_run-06/
!aws s3 sync --no-sign-request s3://openneuro.org/ds001499/sub-CSI3/ses-16/anat/ /content/bold5000/sub-CSI3_anat/

     |████████████████████████████████| 3.8 MB 16.0 MB/s 
     |████████████████████████████████| 8.6 MB 42.7 MB/s 
     |████████████████████████████████| 547 kB 42.4 MB/s 
     |████████████████████████████████| 79 kB 1.4 MB/s 
     |████████████████████████████████| 138 kB 44.3 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
  Attempting uninstall: rsa
    Found existing installation: rsa 4.8
    Uninstalling rsa-4.8:
      Successfully uninstalled rsa-4.8
  Attempting uninstall: docutils
    Found existing installation: docutils 0.17.1
    Uninstalling docutils-0.17.1:
      Successfully uninstalled docutils-0.17.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
requests 2.23.0 requires urllib3!=1.25.0,!=1.25.1,<1.26,>=1.21.1, but you have ur

We add the same auxiliary definitions as last time.

In [2]:
## Auxiliary code for our wavelet experiments
import bokeh
import bokeh.plotting as bpl
from bokeh.models import ColorBar, BasicTicker, LinearColorMapper
import pywt

## Try to do something like imagesc in MATLAB using Bokeh tools.
def imagesc(M, title=''):
  m, n = M.shape
  
  # 600 px should be good; calculate ph to try to get aspect ratio right
  pw = 600
  ph = round(1.0 * pw * m / n)
  h = bpl.figure(plot_width = pw, plot_height = ph, x_range=(0, 1.0*n),
                 y_range=(0, 1.0*m), toolbar_location='below',
                 title=title, match_aspect=True
                )
  
  minval = np.min(M)
  maxval = np.max(M)
  
  color_mapper = LinearColorMapper(palette="Greys256", low=minval, high=maxval)
  h.image(image=[M], x=0, y=0, dw=1.0*n, dh=1.0*m, color_mapper=color_mapper)
  
  color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                      label_standoff=12, border_line_color=None, location=(0, 0))
  
  h.add_layout(color_bar, 'right')
  

  bpl.show(h)
  return h

## Wavelet functions below
## Note: we expect all image sizes to be powers-of-two and square!
## So if you adapt this code, be sure to fix this or enforce this requirement...

# Get a default slice object for a multilevel wavelet transform
# Used to abstract this annoying notation out of the transform...
def default_slices(levels, n):
  c = pywt.wavedec2(np.zeros((n, n)), 'db4', mode='periodization', level=levels)
  bye, slices = pywt.coeffs_to_array(c)
  return slices

# Wrapper for forward discrete wavelet transform
# Output data as a matrix (we don't care about tuple format)
def dwt(levels, sdom_data):
  c = pywt.wavedec2(sdom_data, 'db4', mode='periodization', level=levels)
  output, bye = pywt.coeffs_to_array(c)
  return output

# Wrapper for inverse discrete wavelet transform
# Expect wdom_data as a matrix (we don't care about tuple format)
def idwt(levels, wdom_data, slices=None):
  n = wdom_data.shape[0]
  if slices is None:
    slices = default_slices(levels, n)
  c = pywt.array_to_coeffs(wdom_data, slices, output_format='wavedec2')
  return pywt.waverec2(c, 'db4', mode='periodization')

We finally extract the sagittarial slice we will study. Again, same as last time.

In [3]:
import numpy as np
import nibabel as nib

img = nib.load('/content/bold5000/sub-CSI3_anat/sub-CSI3_ses-16_T1w.nii.gz')

data = img.get_fdata()

## Store dimensions
Nx = data.shape[0]
Ny = data.shape[1]
Nz = data.shape[2]
n = Ny
X = data[Nx//2, :, :];

bpl.output_notebook()
imagesc(data[Nx//2, :, :], title='MR Image We Will Recover')

Figure(id='1002', ...)

## Implementing the Measurement Model

An MR machine collects samples of the 2D Fourier transformation of the underlying spatial profile (e.g., the figure above). An MR machine that employs compressive sensing does the same, but collects far fewer than the `n ** 2` measurements necessary to exactly represent the image at the resolution we are using above. From the lecture, we know that such subsampling leads to an incoherent measurement map when the sampling is done randomly; and we expect thus that L1 minimization will work for recovery from the compressive measurements.

The measurement model we will implement here is the Bernoulli one described in the homework handout. We will implement this below.

In [4]:
## Create the index set for our mapping
p = 0.3   # bernoulli distribution parameter
Omega = {}# We define Omega here to contain all the indices to _delete_
for idx_i in np.arange(n):
  for idx_j in np.arange(n):
    coin = np.random.rand(1,)
    if coin > p:
      Omega[(idx_i, idx_j)] = 1
idxs = np.asarray(list(Omega.keys()))
len(X[idxs[:,0], idxs[:,1]]) # Index like this

## Create the operator
levels = 2
def meas_map(mtx):
  pre_proj = np.fft.fft2(idwt(levels, mtx), norm="ortho")
  pre_proj[idxs[:, 0], idxs[:, 1]] = 0
  return pre_proj
def meas_map_adj(mtx):
  mtx[idxs[:, 0], idxs[:, 1]] = 0
  return dwt(levels, np.fft.ifft2(mtx, norm="ortho"))

## Performing Sparse Recovery

We generate observations `Y` from our input `X` and the measurement map. In particular, we first get the sparse coefficients `S` for our image, and then transform them in order to match with the measurement model.

In [5]:
S = dwt(levels, X)
Y = meas_map(S)

We plot a few observations of our image below.

In [6]:
bpl.output_notebook()
imagesc(np.fft.fftshift(np.abs(np.fft.fft2(X/n**2))))

Figure(id='1114', ...)

Above is the normalized 2D FFT of the image `X`, shifted to have low frequencies in the center of the image. We see that nearly all the frequency content is localized in the low frequencies, and the image appears quite sparse! However, the Fourier phase contains a *lot* of information about the image: reconstructing as we did in the previous homework using large-magnitude wavelet coefficients (but with large magnitude Fourier coefficients here) gives a small squared-error, but a result with poor visual quality, as we can see in the figure below.

In [7]:
F = np.fft.fft2(X)
absmags = np.absolute(F.flatten())
idxs_absmag = np.argsort(absmags)
idxs_absmag = idxs_absmag[::-1] 

num_keep = 8000
F_copy = np.copy(F)
F_copy[np.unravel_index(idxs_absmag[num_keep:], (n, n))] = 0
X_reconstr = np.fft.ifft2(F_copy)

bpl.output_notebook()
imagesc(np.abs(X_reconstr))

Figure(id='1237', ...)

This is what motivates us to use the wavelet transform, and its corresponding notion of sparsity, in our measurement map.

## Your Tasks

Complete each of the tasks in the level three headers below.

### Task 1: Sparse Recovery with Proximal Gradient

For this task, you should implement the proximal gradient descent algorithm for the LASSO objective with the measurement map we have specified in this problem and in the theoretical setting sketched in the homework writeup. Your algorithm will be quite similar to the algorithm you wrote (or will write) for the spectrum sensing application, but you will need to make the necessary changes to the matrix-vector multiplications to accommodate the "matrix linear maps" in this problem. Feel free to change any part of the provided code if you find it more convenient to work with. 

See the first task's description in the spectrum sensing problem for hints about how to code and debug your proximal gradient descent algorithm.

**Hint**: Be sure your choice of initialization matches the scale of the data `Y`. A good practice is to use Gaussian initialization, such that the expected Frobenius norm of the initialization matrix is around 1; then also scale the matrix `Y` to have Frobenius norm 1. You can restore the original scale after you solve the optimization problem.

**Hint**: The algorithm can take a while to run. To speed things up, you may want to code your algorithm wisely by using vectors and matrices operations. For the purpose of testing you can downsample the input MR image, so that instead of being `256 x 256` it is e.g. `64 x 64`. Be sure to keep the sizes as powers of two, or the wavelet transform code will break. This will also help with experimenting to find the best setting of the sparsifying parameter `lambda`: it plays a very large role in the visual quality of the signal you reconstruct. 

In [10]:
Y_normalized = Y / np.linalg.norm(Y , ord = 'fro')
max_iter = 1e3
lambda_list = [0.0001,0.002]

loss_dict = {}
S0_normalized_dict = {}

for lambda1 in lambda_list:

  print(f"For lambda = {lambda1}.....")

  S0 = np.random.normal(0,1,size = Y_normalized.shape)
  S0_normalized = S0 / np.linalg.norm(S0, ord = 'fro')

  alpha = 1

  i = 0
  loss =[]

  while(i < max_iter):
    A = meas_map(S0_normalized)
    grad = meas_map_adj((A - Y_normalized))
    w = S0_normalized - alpha * grad

    magnitude_arr = np.maximum(np.absolute(w) - alpha * lambda1, np.zeros(w.shape))
    phase_arr = np.angle(w)

    S0_normalized = np.multiply(magnitude_arr, np.cos(phase_arr)) + 1j * np.multiply(magnitude_arr, np.sin(phase_arr))
    loss.append((0.5 * (np.linalg.norm(A - Y_normalized) ** 2)) + (lambda1 * sum(sum(np.absolute(S0_normalized)))))
    i += 1  

  S0_normalized_dict[lambda1] = S0_normalized
  loss_dict[lambda1]= loss[-1]
  print(f"The final loss value is: {loss[-1]}")

For lambda = 0.0001.....
The final loss value is: 0.007355146417523739
For lambda = 0.002.....
The final loss value is: 0.11131654275750874


In [11]:
best_lambda = min(loss_dict.keys())
S0_normalized=S0_normalized_dict[best_lambda]

In [12]:
X_pred = idwt(levels,S0_normalized)
bpl.output_notebook()
imagesc(np.abs(X_pred))

Figure(id='1371', ...)

### Task 2: Assessing Performance

Complete the following performance evaluation tasks for your sparse recovery algorithm:
1. For at least 3 values of the Bernoulli parameter `p`, say `[0.1, 0.2, 0.4, 0.5, 0.7]`, perform at least 3 independent trials of the sparse recovery experiment. Here, "independent trials" means you should re-generate the measurement map in each separate experiment. For each experiment, calculate the mean squared error between your LASSO solver's output and the ground truth image `X` (make sure they are in the same domain!), and average the mean squared errors for each setting of `p` over the independent trials. Output a plot of these averaged mean squared errors as a function of `p`; include error bars corresponding to the trial variances.
2. How large do you need `p` to be before you get acceptable (in terms of both MSE and in terms of visual quality) results for the sparse recovery experiment? Can you give an explanation for why the performance may be worse here than in other experiments in terms of properties of the specific measurement map we use here?

### For p =0.1

In [13]:
## Create the index set for our mapping
p = 0.1   # bernoulli distribution parameter
Omega = {}# We define Omega here to contain all the indices to _delete_
for idx_i in np.arange(n):
  for idx_j in np.arange(n):
    coin = np.random.rand(1,)
    if coin > p:
      Omega[(idx_i, idx_j)] = 1
idxs = np.asarray(list(Omega.keys()))
len(X[idxs[:,0], idxs[:,1]]) # Index like this

## Create the operator
levels = 2
def meas_map(mtx):
  pre_proj = np.fft.fft2(idwt(levels, mtx), norm="ortho")
  pre_proj[idxs[:, 0], idxs[:, 1]] = 0
  return pre_proj
def meas_map_adj(mtx):
  mtx[idxs[:, 0], idxs[:, 1]] = 0
  return dwt(levels, np.fft.ifft2(mtx, norm="ortho"))

In [14]:
S = dwt(levels, X)
Y = meas_map(S)

In [16]:
Y_normalized = Y / np.linalg.norm(Y , ord = 'fro')
max_iter = 1e3
lambda_list = [0.0001,0.002]

loss_dict = {}
S0_normalized_dict = {}

for lambda1 in lambda_list:

  print(f"For lambda = {lambda1}.....")

  S0 = np.random.normal(0,1,size = Y_normalized.shape)
  S0_normalized = S0 / np.linalg.norm(S0, ord = 'fro')

  alpha = 1

  i = 0
  loss =[]

  while(i < max_iter):
    A = meas_map(S0_normalized)
    grad = meas_map_adj((A - Y_normalized))
    w = S0_normalized - alpha * grad

    magnitude_arr = np.maximum(np.absolute(w) - alpha * lambda1, np.zeros(w.shape))
    phase_arr = np.angle(w)

    S0_normalized = np.multiply(magnitude_arr, np.cos(phase_arr)) + 1j * np.multiply(magnitude_arr, np.sin(phase_arr))
    loss.append((0.5 * (np.linalg.norm(A - Y_normalized) ** 2)) + (lambda1 * sum(sum(np.absolute(S0_normalized)))))
    i += 1  

  S0_normalized_dict[lambda1] = S0_normalized
  loss_dict[lambda1]= loss[-1]
  print(f"The final loss value is: {loss[-1]}")

For lambda = 0.0001.....
The final loss value is: 0.007940354571268937
For lambda = 0.002.....
The final loss value is: 0.11490990233328112


In [17]:
best_lambda = min(loss_dict.keys())
S0_normalized=S0_normalized_dict[best_lambda]
X_pred = idwt(levels,S0_normalized)
bpl.output_notebook()
imagesc(np.abs(X_pred))

Figure(id='1516', ...)

### For p =0.5

In [18]:
## Create the index set for our mapping
p = 0.5   # bernoulli distribution parameter
Omega = {}# We define Omega here to contain all the indices to _delete_
for idx_i in np.arange(n):
  for idx_j in np.arange(n):
    coin = np.random.rand(1,)
    if coin > p:
      Omega[(idx_i, idx_j)] = 1
idxs = np.asarray(list(Omega.keys()))
len(X[idxs[:,0], idxs[:,1]]) # Index like this

## Create the operator
levels = 2
def meas_map(mtx):
  pre_proj = np.fft.fft2(idwt(levels, mtx), norm="ortho")
  pre_proj[idxs[:, 0], idxs[:, 1]] = 0
  return pre_proj
def meas_map_adj(mtx):
  mtx[idxs[:, 0], idxs[:, 1]] = 0
  return dwt(levels, np.fft.ifft2(mtx, norm="ortho"))

In [19]:
S = dwt(levels, X)
Y = meas_map(S)

In [21]:
Y_normalized = Y / np.linalg.norm(Y , ord = 'fro')
max_iter = 1e3
lambda_list = [0.0001,0.002]

loss_dict = {}
S0_normalized_dict = {}

for lambda1 in lambda_list:

  print(f"For lambda = {lambda1}.....")

  S0 = np.random.normal(0,1,size = Y_normalized.shape)
  S0_normalized = S0 / np.linalg.norm(S0, ord = 'fro')

  alpha = 1

  i = 0
  loss =[]

  while(i < max_iter):
    A = meas_map(S0_normalized)
    grad = meas_map_adj((A - Y_normalized))
    w = S0_normalized - alpha * grad

    magnitude_arr = np.maximum(np.absolute(w) - alpha * lambda1, np.zeros(w.shape))
    phase_arr = np.angle(w)

    S0_normalized = np.multiply(magnitude_arr, np.cos(phase_arr)) + 1j * np.multiply(magnitude_arr, np.sin(phase_arr))
    loss.append((0.5 * (np.linalg.norm(A - Y_normalized) ** 2)) + (lambda1 * sum(sum(np.absolute(S0_normalized)))))
    i += 1  

  S0_normalized_dict[lambda1] = S0_normalized
  loss_dict[lambda1]= loss[-1]
  print(f"The final loss value is: {loss[-1]}")

For lambda = 0.0001.....
The final loss value is: 0.007651008906474811
For lambda = 0.002.....
The final loss value is: 0.11417382818655095


In [22]:
best_lambda = min(loss_dict.keys())
S0_normalized=S0_normalized_dict[best_lambda]
X_pred = idwt(levels,S0_normalized)
bpl.output_notebook()
imagesc(np.abs(X_pred))

Figure(id='1672', ...)

### For p =0.7

In [23]:
## Create the index set for our mapping
p = 0.7   # bernoulli distribution parameter
Omega = {}# We define Omega here to contain all the indices to _delete_
for idx_i in np.arange(n):
  for idx_j in np.arange(n):
    coin = np.random.rand(1,)
    if coin > p:
      Omega[(idx_i, idx_j)] = 1
idxs = np.asarray(list(Omega.keys()))
len(X[idxs[:,0], idxs[:,1]]) # Index like this

## Create the operator
levels = 2
def meas_map(mtx):
  pre_proj = np.fft.fft2(idwt(levels, mtx), norm="ortho")
  pre_proj[idxs[:, 0], idxs[:, 1]] = 0
  return pre_proj
def meas_map_adj(mtx):
  mtx[idxs[:, 0], idxs[:, 1]] = 0
  return dwt(levels, np.fft.ifft2(mtx, norm="ortho"))

In [24]:
S = dwt(levels, X)
Y = meas_map(S)

In [25]:
Y_normalized = Y / np.linalg.norm(Y , ord = 'fro')
max_iter = 1e3
lambda_list = [0.0001,0.002]

loss_dict = {}
S0_normalized_dict = {}

for lambda1 in lambda_list:

  print(f"For lambda = {lambda1}.....")

  S0 = np.random.normal(0,1,size = Y_normalized.shape)
  S0_normalized = S0 / np.linalg.norm(S0, ord = 'fro')

  alpha = 1

  i = 0
  loss =[]

  while(i < max_iter):
    A = meas_map(S0_normalized)
    grad = meas_map_adj((A - Y_normalized))
    w = S0_normalized - alpha * grad

    magnitude_arr = np.maximum(np.absolute(w) - alpha * lambda1, np.zeros(w.shape))
    phase_arr = np.angle(w)

    S0_normalized = np.multiply(magnitude_arr, np.cos(phase_arr)) + 1j * np.multiply(magnitude_arr, np.sin(phase_arr))
    loss.append((0.5 * (np.linalg.norm(A - Y_normalized) ** 2)) + (lambda1 * sum(sum(np.absolute(S0_normalized)))))
    i += 1  

  S0_normalized_dict[lambda1] = S0_normalized
  loss_dict[lambda1]= loss[-1]
  print(f"The final loss value is: {loss[-1]}")

For lambda = 0.0001.....
The final loss value is: 0.006484870358496579
For lambda = 0.002.....
The final loss value is: 0.09704962767551052


In [26]:
best_lambda = min(loss_dict.keys())
S0_normalized=S0_normalized_dict[best_lambda]
X_pred = idwt(levels,S0_normalized)
bpl.output_notebook()
imagesc(np.abs(X_pred))

Figure(id='1839', ...)

2. How large do you need `p` to be before you get acceptable (in terms of both MSE and in terms of visual quality) results for the sparse recovery experiment? Can you give an explanation for why the performance may be worse here than in other experiments in terms of properties of the specific measurement map we use here?

## Answer
As we see after the above tests, for p = 0.7 we see that the value of the error is the least that we obtain. Also this can be seen visually as well as we see that the solution is very clear without haze compared to the others and also each of the parts of brain are seen clearly in the image. We see that higher the value of the p more sparse the solution tends to be because we are forcing the solution to be more sparse. This leads us to giving us the correct solution and prove our underlying assumption at the start that the resultant matrix must be sparse. 